In [1]:
import numpy as np
import pandas as pd
from bs4 import BeautifulSoup
import requests
import json
# import geocoder
import folium
# import sklearn
# from sklearn.cluster import KMeans
# import matplotlib.cm as cm
# import matplotlib.colors as colors
from geopy.geocoders import Nominatim
import time

In [2]:
with open('secrets/foursquare_secrets.json') as f_in: # Load foursquare API credentials
    fsq_secrets = json.load(f_in)

# with open('secrets/geocoder_secrets.json') as f_in: # Load Google API_KEY
#     geo_secrets = json.load(f_in)

CLIENT_SECRET = fsq_secrets['CLIENT_SECRET']
CLIENT_ID = fsq_secrets['CLIENT_ID']
# API_KEY = geo_secrets['API_KEY']
VERSION = '20180605'

In [79]:
test_list_1 = ['abc', 'def', 'ghi']
test_list_2 = ['abc']
test_list_3 = ['abc', 'def']

In [82]:
','.join(test_list_3)

'abc,def'

In [3]:
def get_nearby_venues(lat, lon, category_ids, radius = 500, LIMIT = 100):
    # Foursquare API url for venue queries
    base_url = "https://api.foursquare.com/v2/venues/explore"
    
    # Set up query parameters
    params = {
        'client_id': CLIENT_ID,
        'client_secret': CLIENT_SECRET,
        'v': VERSION,
        'll': '',
        'categoryId': '',
        'radius': radius,
        'limit': LIMIT
    }

    params['ll'] = str(lat) + ',' + str(lon) # Update latitude and longitude
    params['categoryId'] = ','.join(category_ids)
    query = requests.get(base_url, params = params)
    
    return query

In [13]:
def get_lat_lon(location_string, api_key = API_KEY):
    g = geocoder.google(location_string, key = api_key)
    return g.latlng

In [14]:
g = None
count = 0
while not g and count < 100:
    g = get_lat_lon('Mountain View, CA')
    count += 1

In [15]:
g

In [27]:
url = 'https://maps.googleapis.com/maps/api/geocode/json'
params = {'address': 'Mountain View, CA', 'API_KEY': API_KEY}
r = requests.get(url, params = params)

In [28]:
r.json()

{'error_message': 'You must use an API key to authenticate each request to Google Maps Platform APIs. For additional information, please refer to http://g.co/dev/maps-no-account',
 'results': [],
 'status': 'REQUEST_DENIED'}

In [50]:
base_url = "https://public.opendatasoft.com/api/records/1.0/search/"
params = {
    'dataset': 'us-zip-code-latitude-and-longitude',
    'q': 'san francisco',
    'rows': 100
}

In [51]:
r = requests.get(base_url, params = params)

In [52]:
sf_json = r.json()

In [53]:
base_url = "https://public.opendatasoft.com/api/records/1.0/search/"
params = {
    'dataset': 'us-zip-code-latitude-and-longitude',
    'q': 'austin',
    'rows': 100,
    'refine.state': 'TX'
}

In [54]:
r = requests.get(base_url, params = params)

In [55]:
austin_json = r.json()

In [40]:
sf_json['records'][0].keys()

dict_keys(['datasetid', 'recordid', 'fields', 'geometry', 'record_timestamp'])

In [43]:
sf_json['records'][0]['fields']

{'city': 'San Francisco',
 'zip': '94107',
 'dst': 1,
 'geopoint': [37.766529, -122.39577],
 'longitude': -122.39577,
 'state': 'CA',
 'latitude': 37.766529,
 'timezone': -8}

In [57]:
len(sf_json['records'])

74

In [56]:
len(austin_json['records'])

83

In [2]:
sf_lat = 37.7749
sf_lon = -122.4194
austin_lat = 30.2672
austin_lon = -97.7431

In [60]:
sf_map = folium.Map(location = [sf_lat, sf_lon], zoom_start = 11)

for record in sf_json['records']:
    folium.CircleMarker(
        record['fields']['geopoint'],
        radius = 5,
        popup = record['fields']['zip'],
        color = 'green',
        fill = True).add_to(sf_map)

austin_map = folium.Map(location = [austin_lat, austin_lon], zoom_start = 11)

for record in austin_json['records']:
    folium.CircleMarker(
        record['fields']['geopoint'],
        radius = 5,
        popup = record['fields']['zip'],
        color = 'green',
        fill = True).add_to(austin_map)

In [61]:
sf_map

In [63]:
sf_remove = [94140, 94080, 94128, 94083]

In [62]:
austin_map

In [64]:
base_url = "https://public.opendatasoft.com/api/records/1.0/search/"
params = {
    'dataset': 'us-zip-code-latitude-and-longitude',
    'q': 'tampa',
    'rows': 100,
    'refine.state': 'FL'
}

In [65]:
r = requests.get(base_url, params = params)

In [66]:
tampa_json = r.json()

In [67]:
len(tampa_json['records'])

61

In [3]:
tampa_lat = 27.9506
tampa_lon = -82.4572

In [72]:
tampa_map = folium.Map(location = [tampa_lat, tampa_lon], zoom_start = 11)

for record in tampa_json['records']:
    folium.CircleMarker(
        record['fields']['geopoint'],
        radius = 5,
        popup = record['fields']['zip'],
        color = 'green',
        fill = True).add_to(tampa_map)

In [73]:
tampa_map

In [74]:
tampa_remove = [33647, 33643]

In [4]:
fsq_categories = {
    'Fast Food Restaurant': '4bf58dd8d48988d16e941735',
    'Deli/Bodega': '4bf58dd8d48988d146941735',
    'Residence': '4e67e38e036454776db1fb3a',
    'Convenience Store': '4d954b0ea243a5684a65b473',
    'Drugstore': '5745c2e4498e11e7bccabdbd',
    'Food & Drink Shop': '4bf58dd8d48988d1f9941735',
    'Fruit & Vegetable Store': '52f2ab2ebcbc57f1066b8b1c',
    'Gas Station': '4bf58dd8d48988d113951735'
}

In [9]:
with open("variables/fsq_categories.json", 'w') as f_out:
    json.dump(fsq_categories, f_out)

In [78]:
sf_json['records'][0]['fields']

{'city': 'San Francisco',
 'zip': '94107',
 'dst': 1,
 'geopoint': [37.766529, -122.39577],
 'longitude': -122.39577,
 'state': 'CA',
 'latitude': 37.766529,
 'timezone': -8}

In [111]:
sample_entry = 0
sample_city = tampa_json

sample_lat = sample_city['records'][sample_entry]['fields']['latitude']
sample_lon = sample_city['records'][sample_entry]['fields']['longitude']

sample_cats = ['Fast Food Restaurant']

sample_cat_ids = [fsq_categories[cat] for cat in sample_cats]

sample_query = get_nearby_venues(sample_lat, sample_lon, sample_cat_ids, radius = 1500)

In [112]:
sample_json = sample_query.json()

In [116]:
tampa_json['records'][0]

{'datasetid': 'us-zip-code-latitude-and-longitude',
 'recordid': 'e082b8a556d56daa585beedc9402cb69378d9a99',
 'fields': {'city': 'Tampa',
  'zip': '33655',
  'dst': 1,
  'geopoint': [27.871964, -82.438841],
  'longitude': -82.438841,
  'state': 'FL',
  'latitude': 27.871964,
  'timezone': -5},
 'geometry': {'type': 'Point', 'coordinates': [-82.438841, 27.871964]},
 'record_timestamp': '2018-02-09T16:33:38.603000+00:00'}

In [115]:
sample_json['response']

{'warning': {'text': "There aren't a lot of results near you. Try something more general, reset your filters, or expand the search area."},
 'headerLocation': 'Current map view',
 'headerFullLocation': 'Current map view',
 'headerLocationGranularity': 'unknown',
 'query': 'fast food',
 'totalResults': 0,
 'suggestedBounds': {'ne': {'lat': 27.885464013500012,
   'lng': -82.42359791019229},
  'sw': {'lat': 27.858463986499984, 'lng': -82.45408408980771}},
 'groups': [{'type': 'Recommended Places',
   'name': 'recommended',
   'items': []}]}

In [113]:
len(sample_json['response']['groups'][0]['items'])

0

In [109]:
sample_json['response']['groups'][0]['items'][0]['venue']

{'id': '5e1e84e247c34b0008edcd73',
 'name': 'Magnolia Brewing City Bistro',
 'location': {'lat': 37.768485,
  'lng': -122.386724,
  'labeledLatLngs': [{'label': 'display',
    'lat': 37.768485,
    'lng': -122.386724}],
  'distance': 825,
  'postalCode': '94158',
  'cc': 'US',
  'city': 'San Francisco',
  'state': 'CA',
  'country': 'United States',
  'formattedAddress': ['San Francisco, CA 94158', 'United States']},
 'categories': [{'id': '4bf58dd8d48988d16e941735',
   'name': 'Fast Food Restaurant',
   'pluralName': 'Fast Food Restaurants',
   'shortName': 'Fast Food',
   'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/fastfood_',
    'suffix': '.png'},
   'primary': True}],
 'photos': {'count': 0, 'groups': []}}

In [110]:
for item in sample_json['response']['groups'][0]['items']:
    print(item['venue']['name'])

Magnolia Brewing City Bistro
Plow
Subway
Boston Market
McDonald's
Gilroy Garlic Fries
Gluten Free Culture
Taco Bell Cantina
Tender Greens
Dumpling Time
Taqueria
Happy Donuts
GREEN Garlic Fries Concession Stand
Port Walk Pizza
SUBWAY
Doggie Diner
Subway
SUBWAY
Hot Plate


In [117]:
base_url

'https://public.opendatasoft.com/api/records/1.0/search/'

In [120]:
base_url = "https://api.foursquare.com/v2/venues/explore"
    
# Set up query parameters
params = {
    'client_id': CLIENT_ID,
    'client_secret': CLIENT_SECRET,
    'v': VERSION,
#     'll': '',
    'near': '33655',
    'categoryId': fsq_categories['Residence'],
    'radius': 500,
    'limit': 100
}

#     params['ll'] = str(lat) + ',' + str(lon) # Update latitude and longitude
#     params['near'] = 
#     params['categoryId'] = ','.join(category_ids)
query = requests.get(base_url, params = params)
    
#     return query

In [123]:
fl_33655 = query.json()

In [134]:
fl_33655['response']['groups'][0]['items'][0]['venue']

{'id': '4e51258c6284416669a5d199',
 'name': 'Bayshore Boulevard',
 'location': {'lat': 27.911484497747697,
  'lng': -82.4906496720535,
  'labeledLatLngs': [{'label': 'display',
    'lat': 27.911484497747697,
    'lng': -82.4906496720535}],
  'cc': 'US',
  'city': 'Tampa',
  'state': 'FL',
  'country': 'United States',
  'formattedAddress': ['Tampa, FL', 'United States']},
 'categories': [{'id': '4bf58dd8d48988d159941735',
   'name': 'Trail',
   'pluralName': 'Trails',
   'shortName': 'Trail',
   'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/parks_outdoors/hikingtrail_',
    'suffix': '.png'},
   'primary': True}],
 'photos': {'count': 0, 'groups': []}}

In [137]:
sf_json['records'][0]

{'datasetid': 'us-zip-code-latitude-and-longitude',
 'recordid': '2cfe9f10eb823de121721d112cae38ecd734d997',
 'fields': {'city': 'San Francisco',
  'zip': '94107',
  'dst': 1,
  'geopoint': [37.766529, -122.39577],
  'longitude': -122.39577,
  'state': 'CA',
  'latitude': 37.766529,
  'timezone': -8},
 'geometry': {'type': 'Point', 'coordinates': [-122.39577, 37.766529]},
 'record_timestamp': '2018-02-09T16:33:38.603000+00:00'}

In [139]:
for record in sf_json['records']:
    if record['fields']['zip'] == '94122':
        print(record['fields'])

{'city': 'San Francisco', 'zip': '94122', 'dst': 1, 'geopoint': [37.75838, -122.48478], 'longitude': -122.48478, 'state': 'CA', 'latitude': 37.75838, 'timezone': -8}


In [144]:
response = get_nearby_venues(37.764, -122.472, [fsq_categories['Food & Drink Shop']])

In [145]:
response_94122 = response.json()

In [152]:
for item in response_94122['response']['groups'][0]['items']:
    print(item['venue']['name'], item['venue']['location']['formattedAddress'])

Andronico's ['1200 Irving St (at Funston Ave)', 'San Francisco, CA 94122', 'United States']
Eddy's Food Store ['951 Irving St (11th Ave)', 'San Francisco, CA 94122', 'United States']
Irving Subs ['1298 12th Ave (at Irving St)', 'San Francisco, CA 94122', 'United States']
Eight-Twenty-Eight Irving Market ['828 Irving St (btw 9th & 10th)', 'San Francisco, CA 94122', 'United States']


In [160]:
[x['name'] for x in response_94122['response']['groups'][0]['items'][3]['venue']['categories']]

['Grocery Store']

In [163]:
response = get_nearby_venues(37.764, -122.472, [fsq_categories['Food & Drink Shop']], radius = 1000)

In [164]:
response_94122_wider = response.json()

In [166]:
for item in response_94122_wider['response']['groups'][0]['items']:
    print(item['venue']['name'], item['venue']['location']['formattedAddress'])

Andronico's ['1200 Irving St (at Funston Ave)', 'San Francisco, CA 94122', 'United States']
Roxie's Market & Deli ['500 Kirkham St (at 9th Ave)', 'San Francisco, CA 94122', 'United States']
22nd & Irving Market ['2101 Irving St (at 22nd Ave)', 'San Francisco, CA 94122', 'United States']
Eddy's Food Store ['951 Irving St (11th Ave)', 'San Francisco, CA 94122', 'United States']
Golden Bear Trading Company ['1401 6th Ave (at Judah St)', 'San Francisco, CA 94122', 'United States']
Sheng Kee Bakery ['1941 Irving St (at 21st Ave.)', 'San Francisco, CA 94122', 'United States']
Irving Subs ['1298 12th Ave (at Irving St)', 'San Francisco, CA 94122', 'United States']
Eight-Twenty-Eight Irving Market ['828 Irving St (btw 9th & 10th)', 'San Francisco, CA 94122', 'United States']
Inner Sunset Farmers Market ['1320 9th Ave (at Irving St)', 'San Francisco, CA 94122', 'United States']
Wah Lian Supermarket ['1931 Irving St (btwn 20th Ave. & 21st Ave.)', 'San Francisco, CA 94122', 'United States']
Judah

In [171]:
for item in response_94122_wider['response']['groups'][0]['items']:
    print(item['venue']['name'], ': ', item['venue']['categories'][0]['name'])

Andronico's :  Grocery Store
Roxie's Market & Deli :  Sandwich Place
22nd & Irving Market :  Grocery Store
Eddy's Food Store :  Liquor Store
Golden Bear Trading Company :  Grocery Store
Sheng Kee Bakery :  Bakery
Irving Subs :  Sandwich Place
Eight-Twenty-Eight Irving Market :  Grocery Store
Inner Sunset Farmers Market :  Farmers Market
Wah Lian Supermarket :  Grocery Store
Judah Ninth Avenue Liquors :  Liquor Store
Sunrise Irving Market :  Grocery Store
VegeFarm :  Grocery Store
S & B Supermarket :  Grocery Store
Stand-Bi Market :  Liquor Store
23rd & Irving Supermarket :  Grocery Store
Daily Health Organic Veggie Cafe :  Vegetarian / Vegan Restaurant
Easy Money :  Liquor Store
Academy Café :  Café
JT Market :  Liquor Store
New May Cheung Co. :  Farmers Market
Park's Farmers Market :  Farmers Market
Inspire Productions :  Event Service
Heartland Healthy Food :  Health Food Store


In [177]:
print(response_94122_wider['response']['groups'][0]['items'][-1]['venue']['location']['lat'])
print(response_94122_wider['response']['groups'][0]['items'][-1]['venue']['location']['lng'])

37.763121000000005
-122.48226899999999


In [7]:
increments = 0.01

In [8]:
sf_boundaries = {
    'north': 37.808,
    'south': 37.708,
    'east': -122.384,
    'west': -122.510
}

chicago_boundaries = {
    'north': 41.997,
    'south': 41.645,
    'east': -87.524,
    'west': -87.802
}

nyc_boundaries = {
    'north': 40.915,
    'south': 40.496,
    'east': -73.701,
    'west': -74.255
}

In [182]:
np.arange(sf_boundaries['south'], sf_boundaries['north'], increments)

array([37.708, 37.718, 37.728, 37.738, 37.748, 37.758, 37.768, 37.778,
       37.788, 37.798])

In [187]:
map_sf_grid = folium.Map(location = [sf_lat, sf_lon], zoom_start = 12)

for point_lat in np.arange(sf_boundaries['south'], sf_boundaries['north'], increments):
    for point_lon in np.arange(sf_boundaries['west'], sf_boundaries['east'], increments):
        folium.CircleMarker(
        [point_lat, point_lon],
        radius = 3,
        color = 'green',
        fill = True).add_to(map_sf_grid)

map_sf_grid

In [5]:
chicago_lat = 41.881832
chicago_lon = -87.623177

In [195]:
map_chicago_grid = folium.Map(location = [chicago_lat, chicago_lon], zoom_start = 10)

for point_lat in np.arange(chicago_boundaries['south'], chicago_boundaries['north'], increments):
    for point_lon in np.arange(chicago_boundaries['west'], chicago_boundaries['east'], increments):
        folium.CircleMarker(
        [point_lat, point_lon],
        radius = 1.5,
        color = 'green',
        fill = True).add_to(map_chicago_grid)

map_chicago_grid

In [6]:
nyc_lat = 40.730610
nyc_lon = -73.935242

In [199]:
map_nyc_grid = folium.Map(location = [nyc_lat, nyc_lon], zoom_start = 10)

for point_lat in np.arange(nyc_boundaries['south'], nyc_boundaries['north'], increments):
    for point_lon in np.arange(nyc_boundaries['west'], nyc_boundaries['east'], increments):
        folium.CircleMarker(
        [point_lat, point_lon],
        radius = 1.5,
        color = 'green',
        fill = True).add_to(map_nyc_grid)

map_nyc_grid

In [271]:
points_array_nyc = []

for point_lat in np.arange(nyc_boundaries['south'], nyc_boundaries['north'], increments):
    for point_lon in np.arange(nyc_boundaries['west'], nyc_boundaries['east'], increments):
        points_array_nyc.append([point_lat, point_lon])

df = pd.DataFrame(points_array_nyc)
df.to_csv("nyc_grid.csv", index = False)

In [272]:
points_array_sf = []

for point_lat in np.arange(sf_boundaries['south'], sf_boundaries['north'], increments):
    for point_lon in np.arange(sf_boundaries['west'], sf_boundaries['east'], increments):
        points_array_sf.append([point_lat, point_lon])

df = pd.DataFrame(points_array_sf)
df.to_csv("sf_grid.csv", index = False)

In [273]:
points_array_chicago = []

for point_lat in np.arange(chicago_boundaries['south'], chicago_boundaries['north'], increments):
    for point_lon in np.arange(chicago_boundaries['west'], chicago_boundaries['east'], increments):
        points_array_chicago.append([point_lat, point_lon])

df = pd.DataFrame(points_array_chicago)
df.to_csv("chicago_grid.csv", index = False)

In [200]:
base_url = "https://public.opendatasoft.com/api/records/1.0/search/"
params = {
    'dataset': 'us-zip-code-latitude-and-longitude',
    'q': 'chicago',
    'rows': 100,
    'refine.state': 'IL'
}

r = requests.get(base_url, params = params)
chicago_json = r.json()

In [206]:
base_url = "https://public.opendatasoft.com/api/records/1.0/search/"
params = {
    'dataset': 'us-zip-code-latitude-and-longitude',
    'q': 'new york',
    'rows': 200,
    'refine.state': 'NY'
}

r = requests.get(base_url, params = params)
nyc_json = r.json()

In [211]:
nyc_json['records'][0]['fields']['zip']

{'city': 'New York',
 'zip': '10178',
 'dst': 1,
 'geopoint': [40.751378, -73.978507],
 'longitude': -73.978507,
 'state': 'NY',
 'latitude': 40.751378,
 'timezone': -5}

In [217]:
sf_zips = [int(record['fields']['zip']) for record in sf_json['records']]
chicago_zips = [int(record['fields']['zip']) for record in chicago_json['records']]
nyc_zips = [int(record['fields']['zip']) for record in nyc_json['records']]

In [218]:
sf_zips[:5]

[94107, 94152, 94136, 94143, 94146]

In [222]:
sf_df = pd.DataFrame(sf_zips)
sf_df.to_csv("sf_zips.csv", index = False)

In [223]:
chicago_df = pd.DataFrame(chicago_zips)
chicago_df.to_csv("chicago_zips.csv", index = False)

nyc_df = pd.DataFrame(nyc_zips)
nyc_df.to_csv("nyc_zips.csv", index = False)

In [224]:
zip_codes_us_df = pd.read_csv('zip_code_database.csv')

In [240]:
max(zip_codes_us_df[zip_codes_us_df.primary_city == 'San Francisco']['zip'])

94199

In [237]:
city = 'Chicago'
print(len(zip_codes_us_df[zip_codes_us_df.primary_city == city]))

87


In [252]:
max(zip_codes_us_df[(zip_codes_us_df.primary_city == 'San Francisco') & (~zip_codes_us_df.decommissioned)]['zip'])

94188

In [256]:
zip_list_sf = zip_codes_us_df[zip_codes_us_df.primary_city == 'San Francisco'].reset_index()

In [266]:
zip_list_sf[(~zip_list_sf.decommissioned) & (zip_list_sf.type == 'STANDARD')]

index    zip      type  decommissioned   primary_city acceptable_cities  \
1   39680  94102  STANDARD               0  San Francisco               NaN   
2   39681  94103  STANDARD               0  San Francisco               NaN   
3   39682  94104  STANDARD               0  San Francisco               NaN   
4   39683  94105  STANDARD               0  San Francisco               NaN   
6   39685  94107  STANDARD               0  San Francisco               NaN   
7   39686  94108  STANDARD               0  San Francisco               NaN   
8   39687  94109  STANDARD               0  San Francisco               NaN   
9   39688  94110  STANDARD               0  San Francisco               NaN   
10  39689  94111  STANDARD               0  San Francisco               NaN   
11  39690  94112  STANDARD               0  San Francisco               NaN   
12  39691  94114  STANDARD               0  San Francisco               NaN   
13  39692  94115  STANDARD               0  San Francisco               NaN   
14  39693  94116  STANDARD               0  San Francisco               NaN   
15  39694  94117  STANDARD               0  San Francisco               NaN   
16  39695  94118  STANDARD               0  San Francisco               NaN   
19  39698  94121  STANDARD               0  San Francisco               NaN   
20  39699  94122  STANDARD               0  San Francisco               NaN   
21  39700  94123  STANDARD               0  San Francisco               NaN   
22  39701  94124  STANDARD               0  San Francisco               NaN   
25  39704  94127  STANDARD               0  San Francisco               NaN   
26  39705  94128  STANDARD               0  San Francisco               NaN   
27  39706  94129  STANDARD               0  San Francisco               NaN   
28  39707  94130  STANDARD               0  San Francisco               NaN   
29  39708  94131  STANDARD               0  San Francisco               NaN   
30  39709  94132  STANDARD               0  San Francisco               NaN   
31  39710  94133  STANDARD               0  San Francisco               NaN   
32  39711  94134  STANDARD               0  San Francisco               NaN   
53  39732  94158  STANDARD               0  San Francisco               NaN   

            unacceptable_cities state                county  \
1                           NaN    CA  San Francisco County   
2                           NaN    CA  San Francisco County   
3                           NaN    CA  San Francisco County   
4                           NaN    CA  San Francisco County   
6                           NaN    CA  San Francisco County   
7                           NaN    CA  San Francisco County   
8                           NaN    CA  San Francisco County   
9                           NaN    CA  San Francisco County   
10                          NaN    CA  San Francisco County   
11                          NaN    CA  San Francisco County   
12                          NaN    CA  San Francisco County   
13                          NaN    CA  San Francisco County   
14                          NaN    CA  San Francisco County   
15                          NaN    CA  San Francisco County   
16                          NaN    CA  San Francisco County   
19                          NaN    CA  San Francisco County   
20                          NaN    CA  San Francisco County   
21                          NaN    CA  San Francisco County   
22                          NaN    CA  San Francisco County   
25                          NaN    CA  San Francisco County   
26  San Francisco Intnl Airport    CA      San Mateo County   
27                     Presidio    CA  San Francisco County   
28                          NaN    CA  San Francisco County   
29                          NaN    CA  San Francisco County   
30                          NaN    CA  San Francisco County   
31                          NaN    CA  San Francisco County   
32         

In [261]:
zip_codes_us_df[zip_codes_us_df.zip == 94177]

zip    type  decommissioned   primary_city acceptable_cities  \
39742  94177  UNIQUE               0  San Francisco               NaN   

      unacceptable_cities state                county             timezone  \
39742                Pg&e    CA  San Francisco County  America/Los_Angeles   

      area_codes world_region country  latitude  longitude  \
39742        415          NaN      US     37.79    -122.39   

       irs_estimated_population_2015  
39742                              0

In [254]:
zip_codes_us_df['type'].unique()

array(['UNIQUE', 'STANDARD', 'PO BOX', 'MILITARY'], dtype=object)

In [270]:
city_nickname = 'nyc'
city = 'New York'

df_city = zip_codes_us_df[zip_codes_us_df.primary_city == city].reset_index()
df_filtered = df_city[(~df_city.decommissioned) & (df_city.type == 'STANDARD')]

df_filtered[['zip']].to_csv(f"zip_list_{city_nickname}.csv", index = False)

In [277]:
city_nickname = 'sf'
city = 'San Francisco'

df_city = zip_codes_us_df[zip_codes_us_df.primary_city == city].reset_index()
df_filtered = df_city[(~df_city.decommissioned) & (df_city.type == 'STANDARD')]

In [278]:
df_filtered

index    zip      type  decommissioned   primary_city acceptable_cities  \
1   39680  94102  STANDARD               0  San Francisco               NaN   
2   39681  94103  STANDARD               0  San Francisco               NaN   
3   39682  94104  STANDARD               0  San Francisco               NaN   
4   39683  94105  STANDARD               0  San Francisco               NaN   
6   39685  94107  STANDARD               0  San Francisco               NaN   
7   39686  94108  STANDARD               0  San Francisco               NaN   
8   39687  94109  STANDARD               0  San Francisco               NaN   
9   39688  94110  STANDARD               0  San Francisco               NaN   
10  39689  94111  STANDARD               0  San Francisco               NaN   
11  39690  94112  STANDARD               0  San Francisco               NaN   
12  39691  94114  STANDARD               0  San Francisco               NaN   
13  39692  94115  STANDARD               0  San Francisco               NaN   
14  39693  94116  STANDARD               0  San Francisco               NaN   
15  39694  94117  STANDARD               0  San Francisco               NaN   
16  39695  94118  STANDARD               0  San Francisco               NaN   
19  39698  94121  STANDARD               0  San Francisco               NaN   
20  39699  94122  STANDARD               0  San Francisco               NaN   
21  39700  94123  STANDARD               0  San Francisco               NaN   
22  39701  94124  STANDARD               0  San Francisco               NaN   
25  39704  94127  STANDARD               0  San Francisco               NaN   
26  39705  94128  STANDARD               0  San Francisco               NaN   
27  39706  94129  STANDARD               0  San Francisco               NaN   
28  39707  94130  STANDARD               0  San Francisco               NaN   
29  39708  94131  STANDARD               0  San Francisco               NaN   
30  39709  94132  STANDARD               0  San Francisco               NaN   
31  39710  94133  STANDARD               0  San Francisco               NaN   
32  39711  94134  STANDARD               0  San Francisco               NaN   
53  39732  94158  STANDARD               0  San Francisco               NaN   

            unacceptable_cities state                county  \
1                           NaN    CA  San Francisco County   
2                           NaN    CA  San Francisco County   
3                           NaN    CA  San Francisco County   
4                           NaN    CA  San Francisco County   
6                           NaN    CA  San Francisco County   
7                           NaN    CA  San Francisco County   
8                           NaN    CA  San Francisco County   
9                           NaN    CA  San Francisco County   
10                          NaN    CA  San Francisco County   
11                          NaN    CA  San Francisco County   
12                          NaN    CA  San Francisco County   
13                          NaN    CA  San Francisco County   
14                          NaN    CA  San Francisco County   
15                          NaN    CA  San Francisco County   
16                          NaN    CA  San Francisco County   
19                          NaN    CA  San Francisco County   
20                          NaN    CA  San Francisco County   
21                          NaN    CA  San Francisco County   
22                          NaN    CA  San Francisco County   
25                          NaN    CA  San Francisco County   
26  San Francisco Intnl Airport    CA      San Mateo County   
27                     Presidio    CA  San Francisco County   
28                          NaN    CA  San Francisco County   
29                          NaN    CA  San Francisco County   
30                          NaN    CA  San Francisco County   
31                          NaN    CA  San Francisco County   
32         

In [281]:
map_sf = folium.Map(location = [sf_lat, sf_lon], zoom_start = 12)

for lat, lon in zip(df_filtered['latitude'], df_filtered['longitude']):
    folium.CircleMarker(
        [lat, lon],
        radius = 3,
        color = 'blue',
        fill = True).add_to(map_sf)

map_sf

In [283]:
from geopy.geocoders import Nominatim
geolocator = Nominatim(user_agent = 'bridgette.lafaye@gmail.com')

In [284]:
location = geolocator.reverse("37.76, -122.39")

In [286]:
location.raw

{'place_id': 157335371,
 'licence': 'Data © OpenStreetMap contributors, ODbL 1.0. https://osm.org/copyright',
 'osm_type': 'way',
 'osm_id': 274390043,
 'lat': '37.75997125',
 'lon': '-122.39009914113593',
 'display_name': '825, Minnesota Street, Dogpatch, San Francisco, San Francisco City and County, San Francisco, California, 41907, United States',
 'address': {'house_number': '825',
  'road': 'Minnesota Street',
  'neighbourhood': 'Dogpatch',
  'city': 'San Francisco',
  'county': 'San Francisco',
  'state': 'California',
  'postcode': '41907',
  'country': 'United States',
  'country_code': 'us'},
 'boundingbox': ['37.7599007', '37.7600235', '-122.390277', '-122.3899228']}

In [292]:
points_array_sf[0]

[37.708, -122.51]

In [294]:
location = geolocator.reverse("{0}, {1}".format(points_array_sf[0][0], points_array_sf[0][1]))

In [302]:
location.raw

{'place_id': 258123554,
 'licence': 'Data © OpenStreetMap contributors, ODbL 1.0. https://osm.org/copyright',
 'osm_type': 'relation',
 'osm_id': 396498,
 'lat': '37.496904',
 'lon': '-122.3330573',
 'display_name': 'San Mateo County, California, United States',
 'address': {'county': 'San Mateo County',
  'state': 'California',
  'country': 'United States',
  'country_code': 'us'},
 'boundingbox': ['37.0479139', '37.7082836', '-122.588177', '-122.081701']}

In [288]:
map_sf = folium.Map(location = [sf_lat, sf_lon], zoom_start = 12)

folium.CircleMarker(
    points_array_sf[0],
    radius = 3,
    color = 'blue',
    fill = True).add_to(map_sf)

map_sf

In [300]:
len(points_array_sf)

143

In [303]:
time.sleep(1.5)

In [304]:
locations = []

for i, point in enumerate(points_array_sf):
    location = geolocator.reverse("{0}, {1}".format(point[0], point[1]))
    locations.append(location)
    
    if i % 10 == 0:
        print(i)
    
    time.sleep(1.5)

0
10
20
30
40
50
60
70
80
90
100
110
120
130
140


In [305]:
locations_sf = locations

In [321]:
locations[0].raw['lon']

'-122.3330573'

In [350]:
unique_postcodes_sf = {}
keep_sf = []
ignore_sf = []
for location in locations_sf:
    coords = [float(location.raw['lat']), float(location.raw['lon'])]
    point_address = location.raw['address']
    if 'city' in point_address.keys() and 'postcode' in point_address.keys():
        point_city = point_address['city']
        if point_city == 'San Francisco':
            keep_sf.append(coords)
        else:
            ignore_sf.append(coords)
    else:
        ignore_sf.append(coords)

In [351]:
len(ignore_sf)

9

In [332]:
keep_sf[0]

[37.70779534205016, -122.49836619931081]

In [352]:
map_sf = folium.Map(location = [sf_lat, sf_lon], zoom_start = 12)

for point in keep_sf:
    folium.CircleMarker(
        point,
        radius = 3,
        color = 'green',
        fill = True).add_to(map_sf)

for point in ignore_sf:
    folium.CircleMarker(
        point,
        radius = 3,
        color = 'red', 
        fill = True).add_to(map_sf)

map_sf

In [346]:
locations_sf[15].raw

{'place_id': 90605509,
 'licence': 'Data © OpenStreetMap contributors, ODbL 1.0. https://osm.org/copyright',
 'osm_type': 'way',
 'osm_id': 16753068,
 'lat': '37.7216512',
 'lon': '-122.48908601192815',
 'display_name': 'TPC Harding Park, 99, Harding Road, San Francisco, San Francisco City and County, San Francisco, California, 94132, United States',
 'address': {'leisure': 'TPC Harding Park',
  'house_number': '99',
  'road': 'Harding Road',
  'city': 'San Francisco',
  'county': 'San Francisco',
  'state': 'California',
  'postcode': '94132',
  'country': 'United States',
  'country_code': 'us'},
 'boundingbox': ['37.7168277', '37.7267955', '-122.4986714', '-122.484584']}

In [347]:
locations_sf[15].raw['address']['city']

'San Francisco'

In [354]:
keep_sf_df = pd.DataFrame(keep_sf)
keep_sf_df.to_csv("final_grid_sf.csv")

In [357]:
len(points_array_chicago)

1008

In [356]:
len(points_array_nyc[2000:2400])

352

In [363]:
nyc_batches = {}
batch_size = 400

total = len(points_array_nyc)
batch = 0
while batch * batch_size < total:
    print(batch * batch_size, (batch + 1) * batch_size)
    nyc_batches[str(batch)] = points_array_nyc[(batch * batch_size):((batch + 1) * batch_size)]
    batch += 1

0 400
400 800
800 1200
1200 1600
1600 2000
2000 2400


In [373]:
chicago_batches = {}
batch_size = 200

total = len(points_array_chicago)
batch = 0
while batch * batch_size < total:
    print(batch * batch_size, (batch + 1) * batch_size)
    chicago_batches[str(batch)] = points_array_chicago[(batch * batch_size):((batch + 1) * batch_size)]
    batch += 1

0 200
200 400
400 600
600 800
800 1000
1000 1200


In [377]:
len(chicago_batches['1'] + chicago_batches['2'])

400

In [384]:
# locations_chicago = []

for i, point in enumerate(chicago_batches['5']):
    location = geolocator.reverse("{0}, {1}".format(point[0], point[1]))
    locations_chicago.append(location)
    
    if i % 10 == 0:
        print(i)
    
    time.sleep(1.5)

0


In [385]:
locations_chicago[-1]

Location(Cook County, Illinois, United States, (41.8197385, -87.756525, 0.0))

In [386]:
len(locations_chicago)

1008

In [417]:
# locations_nyc = []

for i, point in enumerate(nyc_batches['5']):
    location = geolocator.reverse("{0}, {1}".format(point[0], point[1]))
    locations_nyc.append(location)
    
    if i % 10 == 0:
        print(i)
    
    time.sleep(1.5)

0
10
20
30
40
50
60
70
80
90
100
110
120
130
140
150
160
170
180
190
200
210
220
230
240
250
260
270
280
290
300
310
320
330
340
350


In [418]:
locations_nyc[-1]

Location(Rye, Westchester County, New York, 10580, United States, (40.9808209, -73.684294, 0.0))

In [419]:
len(locations_nyc)

2352

In [427]:
locations_chicago[20].raw

{'place_id': 302808356,
 'licence': 'Data © OpenStreetMap contributors, ODbL 1.0. https://osm.org/copyright',
 'osm_type': 'way',
 'osm_id': 210688357,
 'lat': '41.6449449',
 'lon': '-87.60141735714285',
 'display_name': '826, East 138th Street, Riverdale, Chicago, Thornton Township, Cook County, Illinois, 60827, United States',
 'address': {'house_number': '826',
  'road': 'East 138th Street',
  'suburb': 'Riverdale',
  'city': 'Chicago',
  'municipality': 'Thornton Township',
  'county': 'Cook County',
  'state': 'Illinois',
  'postcode': '60827',
  'country': 'United States',
  'country_code': 'us'},
 'boundingbox': ['41.6448813', '41.6449933', '-87.6015124', '-87.6013698']}

In [472]:
keep_chicago = []
ignore_chicago = []
tmp_chicago = []

for i, location in enumerate(locations_chicago):
    coords = [float(location.raw['lat']), float(location.raw['lon'])]
    point_address = location.raw['address']
    if 'city' in point_address.keys() and 'postcode' in point_address.keys():
        point_city = point_address['city']
        if point_city == 'Chicago':
            keep_chicago.append((i, coords))
        else:
            ignore_chicago.append((i, coords))
    else:
        if 'suburb' in point_address and point_address['suburb'] == 'Loop':
            keep_chicago.append((i, coords))
        else:
            ignore_chicago.append((i, coords))

In [486]:
keep_chicago = []
ignore_chicago = []
# tmp_chicago = []

for i, location in enumerate(locations_chicago):
    coords = [float(location.raw['lat']), float(location.raw['lon'])]
    point_address = location.raw['address']
    if 'city' in point_address.keys() and 'postcode' in point_address.keys():
        point_city = point_address['city']
        if point_city == 'Chicago':
            if 'man_made' in point_address:
#                 ignore_chicago.append((i, coords))
                ignore_chicago.append(coords)
            else:
#                 keep_chicago.append((i, coords))
                keep_chicago.append(coords)
        else:
#             ignore_chicago.append((i, coords))
            ignore_chicago.append(coords)
    else:
        if 'suburb' in point_address and point_address['suburb'] == 'Loop':
            if 'man_made' in point_address:
#                 ignore_chicago.append((i, coords))
                ignore_chicago.append(coords)
            else:
#                 keep_chicago.append((i, coords))
                keep_chicago.append(coords)
        else:
#             ignore_chicago.append((i, coords))
            ignore_chicago.append(coords)

In [487]:
len(keep_chicago) + len(ignore_chicago) + len(tmp_chicago)

1008

In [480]:
map_chicago = folium.Map(location = [chicago_lat, chicago_lon], zoom_start = 11)

for i, point in keep_chicago:
    folium.CircleMarker(
        point,
        radius = 2.5,
        popup = str(i),
        color = 'green',
        fill = True).add_to(map_chicago)

# for i, point in tmp_chicago:
#     folium.CircleMarker(
#         point,
#         radius = 2.5,
#         popup = str(i),
#         color = 'blue',
#         fill = True).add_to(map_chicago)

# for i, point in ignore_chicago:
#     folium.CircleMarker(
#         point,
#         radius = 2.5,
#         popup = str(i),
#         color = 'red', 
#         fill = True).add_to(map_chicago)

map_chicago

In [467]:
locations_chicago[689].raw

{'place_id': 145404114,
 'licence': 'Data © OpenStreetMap contributors, ODbL 1.0. https://osm.org/copyright',
 'osm_type': 'way',
 'osm_id': 230620416,
 'lat': '41.88516465',
 'lon': '-87.63171906033915',
 'display_name': 'Pedway, Loop, Chicago, Cook County, Illinois, United States',
 'address': {'road': 'Pedway',
  'suburb': 'Loop',
  'city': 'Chicago',
  'county': 'Cook County',
  'state': 'Illinois',
  'country': 'United States',
  'country_code': 'us'},
 'boundingbox': ['41.8848719', '41.885459', '-87.632113', '-87.631324']}

In [456]:
count_loop = 0
count_crib = 0
for i, location in enumerate(locations_chicago):
    if 'suburb' in location.raw['address'] and location.raw['address']['suburb'] == 'Loop':
#         count_loop += 1
        print(i)
#     if 'man_made' in location.raw['address']:
#         count_crib += 1

# print(count_loop)
# print(count_crib)

661
662
663
689
690
691


In [488]:
len(keep_chicago)

595

In [489]:
keep_chicago_df = pd.DataFrame(keep_chicago)
keep_chicago_df.to_csv("final_grid_chicago.csv")

In [490]:
locations_nyc[100].raw

{'place_id': 2581697,
 'licence': 'Data © OpenStreetMap contributors, ODbL 1.0. https://osm.org/copyright',
 'osm_type': 'node',
 'osm_id': 357597577,
 'lat': '40.607049',
 'lon': '-73.8090228',
 'display_name': 'Winhole Hassock, New York, 11693, United States',
 'address': {'place': 'Winhole Hassock',
  'city': 'New York',
  'state': 'New York',
  'postcode': '11693',
  'country': 'United States',
  'country_code': 'us'},
 'boundingbox': ['40.287049', '40.927049', '-74.1290228', '-73.4890228']}

In [529]:
keep_nyc = []
ignore_nyc = []

names_to_ignore = ['Swinburne Island', 
                   'West Bank Light', 
#                    'Manhattan Community Board 1', 
                   'Ellis Island Immigration Museum']

for i, location in enumerate(locations_nyc):
    coords = [float(location.raw['lat']), float(location.raw['lon'])]
    point_address = location.raw['address']
    if 'city' in point_address.keys() and 'postcode' in point_address.keys():
        point_city = point_address['city']
        if point_city == 'New York' and 'man_made' not in point_address:
            ignore_flag = False
            for name in names_to_ignore:
                if name in location.raw['display_name']:
                    ignore_flag = True
                    break
            if not ignore_flag:
#                 keep_nyc.append((i, coords))
                keep_nyc.append(coords)
            else:
#                 ignore_nyc.append((i, coords))
                ignore_nyc.append(coords)
        else:
#             ignore_nyc.append((i, coords))
            ignore_nyc.append(coords)
    else:
#         ignore_nyc.append((i, coords))
        ignore_nyc.append(coords)

In [530]:
len(keep_nyc) + len(ignore_nyc)

2352

In [528]:
map_nyc = folium.Map(location = [nyc_lat, nyc_lon], zoom_start = 10)

for i, point in keep_nyc:
    folium.CircleMarker(
        point,
        radius = 2.5,
        popup = str(i),
        color = 'green',
        fill = True).add_to(map_nyc)

# for i, point in tmp_chicago:
#     folium.CircleMarker(
#         point,
#         radius = 2.5,
#         popup = str(i),
#         color = 'blue',
#         fill = True).add_to(map_chicago)

# for i, point in ignore_nyc:
#     folium.CircleMarker(
#         point,
#         radius = 2.5,
#         popup = str(i),
#         color = 'red', 
#         fill = True).add_to(map_nyc)

map_nyc

In [522]:
locations_nyc[1085].raw

{'place_id': 167371625,
 'licence': 'Data © OpenStreetMap contributors, ODbL 1.0. https://osm.org/copyright',
 'osm_type': 'way',
 'osm_id': 320781493,
 'lat': '40.688590928930125',
 'lon': '-74.04451218506138',
 'display_name': 'Manhattan Community Board 1, Manhattan, New York County, New York, 07302-4522, United States',
 'address': {'neighbourhood': 'Manhattan Community Board 1',
  'suburb': 'Manhattan',
  'county': 'New York County',
  'city': 'New York',
  'state': 'New York',
  'postcode': '07302-4522',
  'country': 'United States',
  'country_code': 'us'},
 'boundingbox': ['40.6885651', '40.6907581', '-74.0468035', '-74.0435179']}

In [531]:
keep_nyc_df = pd.DataFrame(keep_nyc)
keep_nyc_df.to_csv("final_grid_nyc.csv")

In [532]:
len(keep_nyc)

1036

In [16]:
keep_sf_df = (pd.read_csv("final_grid_sf.csv")
                   .drop(columns = ['Unnamed: 0'])
                   .rename(columns = {'0': 'latitude', '1': 'longitude'}))

keep_chicago_df = (pd.read_csv("final_grid_chicago.csv")
                   .drop(columns = ['Unnamed: 0'])
                   .rename(columns = {'0': 'latitude', '1': 'longitude'}))

keep_nyc_df = (pd.read_csv("final_grid_nyc.csv")
                   .drop(columns = ['Unnamed: 0'])
                   .rename(columns = {'0': 'latitude', '1': 'longitude'}))

In [19]:
keep_sf_df

latitude   longitude
0    37.709087 -122.493032
1    37.709565 -122.477403
2    37.708501 -122.469934
3    37.708267 -122.460250
4    37.708340 -122.450301
..         ...         ...
129  37.808358 -122.430222
130  37.807778 -122.420196
131  37.807769 -122.409600
132  37.805793 -122.400955
133  37.800206 -122.401082

[134 rows x 2 columns]

### Call Foursquare venues for each coordinate point - SF

In [20]:
increments # about 1000 meters between adjacent points

0.01

In [29]:
radius = 750

In [39]:
fsq_results_list_sf = []

for lat, lon in zip(keep_sf_df['latitude'], keep_sf_df['longitude']):
    query = get_nearby_venues(lat, lon, [fsq_categories['Food & Drink Shop']], radius = radius)
    if query.status_code != 200:
        break
    fsq_results_list_sf.append(query)

In [40]:
len(fsq_results_list_sf)

134

In [51]:
fsq_results_json_sf = [x.json() for x in fsq_results_list_sf]

In [53]:
fsq_results_json_sf[0]

{'meta': {'code': 200, 'requestId': '60b7e63649d56e7e7e4848d0'},
 'response': {'warning': {'text': "There aren't a lot of results near you. Try something more general, reset your filters, or expand the search area."},
  'headerLocation': 'Lakeshore',
  'headerFullLocation': 'Lakeshore, San Francisco',
  'headerLocationGranularity': 'neighborhood',
  'query': 'food drink',
  'totalResults': 0,
  'suggestedBounds': {'ne': {'lat': 37.71583700675, 'lng': -122.4845161745519},
   'sw': {'lat': 37.70233699324999, 'lng': -122.50154860465851}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': []}]}}

In [54]:
with open("sf_venues_results.json", "w") as outfile:
    json.dump(fsq_results_json_sf, outfile)

In [7]:
city_centers = {
    'sf': (sf_lat, sf_lon),
    'chicago': (chicago_lat, chicago_lon),
    'nyc': (nyc_lat, nyc_lon)
}

with open("variables/city_centers.json", 'w') as f_out:
    json.dump(city_centers, f_out)